# Multi lable classification
As the first task of this assignment, you will build a
multi-class classification model. Split the images in the
train directory into a train and a validation dataset and use
them to train a model that given the image of a pedestrian
predicts the following attributes:
- gender
- hair length
- sleeve length
- length of lower-body clothing
- type of lower-body clothing
- wearing hat
- carrying backpack
- carrying bag
- carrying handbag
- age
- color of upper-body clothing
- color of lower-body clothing

The annotations for these attributes are present in the annotations train.csv file and an example is shown in Fig. 2.
Note that the annotation for the color of upper-body clothing and the color of lower-body clothing is not always
present. This corresponds to images where the pedestrian
wears clothes of multiple colors, eg. stripes. To address this
issue please add to the dataset an extra category for color
of upper-body clothing and color of lower-body clothing
that corresponds to multicolor clothing. This is the correct category to predict each time the annotation is missing. Evaluate the performance of the model for each attribute using the validation set. Once validation is completed you are required to produce predictions for each image in the test directory. Produce a classification test.csv
file following the same format as annotations train.csv containing your predictions. Under the id field, instead of reporting the person id, which is unknown for the test set,
please report the exact name of the file the predictions refer
to, eg. 001609.jpg. Note that the test directory also contains
distractor and junk images. Please ignore this fact and produce predictions for them as if they were valid pedestrian
images. For bonus points, you may describe how to modify
your classifier to automatically detect such instances.

## Settings

I mount google drive and move all the directory from gdrive to the machine I'm working on in order to have better access to the data

In [1]:
import zipfile
from google.colab import drive

drive.mount('/content/drive')

Mounted at /content/drive


In [2]:
%cp ./drive/MyDrive/DL/dataset.zip ./

In [3]:
with zipfile.ZipFile('dataset.zip', 'r') as zip_ref:
    zip_ref.extractall('./')

In [4]:
!pip install -Uqq fastbook
import fastbook
fastbook.setup_book()

     |████████████████████████████████| 720 kB 9.8 MB/s 
     |████████████████████████████████| 46 kB 5.4 MB/s 
     |████████████████████████████████| 189 kB 62.6 MB/s 
     |████████████████████████████████| 1.2 MB 75.1 MB/s 
     |████████████████████████████████| 56 kB 5.5 MB/s 
     |████████████████████████████████| 51 kB 415 kB/s 
Mounted at /content/gdrive


In [5]:
## Import libraries in python
import os
os.environ['CUDA_LAUNCH_BLOCKING'] = "1"
import argparse
import time
import json
import sys
import io
import math
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import random
import torch
import glob
import torch.nn as nn
from torchvision.transforms import transforms
from torchvision.utils import make_grid
from torch.utils.tensorboard import SummaryWriter
from torch.utils.data import DataLoader, Dataset
from torch.optim import Adam
from torch.autograd import Variable
from PIL import Image
import torchvision.transforms as tt
from tqdm.notebook import tqdm
import sklearn
import torchvision
import pathlib 
import glob
from fastai.vision.all import *
from sklearn import preprocessing
from skimage import io, transform
from sklearn.preprocessing import OneHotEncoder, LabelEncoder

# Ignore warnings
import warnings
warnings.filterwarnings("ignore")

In [6]:
# Setting Colab 
run_drive = False
if (run_drive):
  from google.colab import drive
  drive.mount('/content/drive')
  current_dir = './drive/MyDrive/DL/dataset'
else:
  # Path settings
  current_dir = '.'

## Dataset path
train_path = current_dir +'/train'
test_path = current_dir +'/test'
queries_path = current_dir +'/queries'
images_path = [train_path, test_path, queries_path]
annotation_path = current_dir +'/annotations_train.csv'

## temporary model path for NN
model_path = current_dir +'/Classification_net.pth'
# Checking for device
device = torch.device('cuda:0' if torch.cuda.is_available() else 'cpu')
print(device)

cuda:0


# Defining classes

## Dataset for Market 1501

In [7]:
class Dataset1501(Dataset):
  """
  Market 1501 dataset for training and validation
  """

  def __init__(self, csv_file, root_dir, transform=None):
      """
      Args:
          csv_file (string): Path to the csv file with annotations(csv path).
          root_dir (string): Directory with all the images (train_path).
          transform (callable, optional): Optional transform to be applied
              on a sample.
      """
      self.df = pd.read_csv(csv_file)
      self.root_dir = root_dir
      self.transform = transform
      print('root_dir: {}'.format(self.root_dir))
      print('csv_file: {}'.format(csv_file))

  def __len__(self):
      return len(self.df)
  
  def __getitem__(self, idx):
      if torch.is_tensor(idx):
          idx = idx.tolist()

      img_name = os.path.join(self.root_dir,
                              str(self.df.iloc[idx, 0]))
      image = io.imread(img_name)
      
      sample = {
          'pic': image, 
          'lables': {
              'hat': np.array(self.df.iloc[idx,1]).astype('float'),
              'handbag': np.array(self.df.iloc[idx,2]).astype('float'),
              'bag': np.array(self.df.iloc[idx,3]).astype('float'),
              'backpack': np.array(self.df.iloc[idx,4]).astype('float'),
              'up': np.array(self.df.iloc[idx,5]).astype('float'),
              'downcolor': np.array(self.df.iloc[idx,6]).astype('float'),
              'clothes': np.array(self.df.iloc[idx,7]).astype('float'),
              'age': np.array(self.df.iloc[idx,8]).astype('float'),
              'down': np.array(self.df.iloc[idx,9]).astype('float'),
              'gender': np.array(self.df.iloc[idx,10]).astype('float'),
              'upcolor': np.array(self.df.iloc[idx,11]).astype('float'),
              'hair': np.array(self.df.iloc[idx,12]).astype('float')
            }
          }

      if self.transform:
          sample['pic'] = self.transform(sample['pic'])

      return sample

class TestDataset1501(Dataset):
  """
  Market 1501 dataset for testing
  """

  def __init__(self, csv_file, root_dir, transform=None):
      """
      Args:
          csv_file (string): Path to the csv file with test annotations(csv path).
          root_dir (string): Directory with all the images (test_path).
          transform (callable, optional): Optional transform to be applied
              on a sample.
      """
      self.df = pd.read_csv(csv_file)
      self.root_dir = root_dir
      self.transform = transform

  def __len__(self):
      return len(self.df)

  def __getitem__(self, idx):
      if torch.is_tensor(idx):
          idx = idx.tolist()

      image_path = os.path.join(self.root_dir,
                              str(self.df.iloc[idx, 0]))
      image = io.imread(image_path)
      
      sample = {
          'pic': image, 
          'filename': self.df.iloc[idx,0],
          'path': image_path
          }

      if self.transform:
          sample['pic'] = self.transform(sample['pic'])

      return sample

## Custom class for ResNet50 model

In [8]:
class CustomRNet50(nn.Module):
  """
  New Custom ResNet50.
  The class takes care of instantiating a new version of ResNet50.
  """
  def __init__(self, boolean = 2, age = 4, upcolor = 9 , downcolor = 10, dropout=0.5):
    """
    Extract the feature extractor from the original model.
    Then are added as many Linear classifier as the number of classes to predict
    """
    super(CustomRNet50, self).__init__()
    # Instantiate a model
    model = torchvision.models.resnet50(pretrained=True)
    self.in_features = model.fc.in_features
    layers = list(model.children())[:-1]
    #Create a feature extractor
    self.feature_extractor = nn.Sequential(*layers)

    # Single classifier for each class
    self.hat          = nn.Sequential(nn.Dropout(p=dropout), 
                             nn.Linear(self.in_features,1000), 
                             nn.ReLU(), 
                             nn.Dropout(p=dropout), 
                             nn.Linear(1000,boolean))
    self.handbag      = nn.Sequential(nn.Dropout(p=dropout), nn.Linear(self.in_features,1000), nn.ReLU(), nn.Dropout(p=dropout), nn.Linear(1000,boolean))
    self.bag          = nn.Sequential(nn.Dropout(p=dropout), nn.Linear(self.in_features,1000), nn.ReLU(), nn.Dropout(p=dropout), nn.Linear(1000,boolean))
    self.bagpack      = nn.Sequential(nn.Dropout(p=dropout), nn.Linear(self.in_features,1000), nn.ReLU(), nn.Dropout(p=dropout), nn.Linear(1000,boolean))
    self.up           = nn.Sequential(nn.Dropout(p=dropout), nn.Linear(self.in_features,1000), nn.ReLU(), nn.Dropout(p=dropout), nn.Linear(1000,boolean))
    self.downcolor    = nn.Sequential(nn.Dropout(p=dropout), nn.Linear(self.in_features,1000), nn.ReLU(), nn.Dropout(p=dropout), nn.Linear(1000,downcolor))
    self.clothes      = nn.Sequential(nn.Dropout(p=dropout), nn.Linear(self.in_features,1000), nn.ReLU(), nn.Dropout(p=dropout), nn.Linear(1000,boolean))
    self.age          = nn.Sequential(nn.Dropout(p=dropout), nn.Linear(self.in_features,1000), nn.ReLU(), nn.Dropout(p=dropout), nn.Linear(1000,age))
    self.down         = nn.Sequential(nn.Dropout(p=dropout), nn.Linear(self.in_features,1000), nn.ReLU(), nn.Dropout(p=dropout), nn.Linear(1000,boolean))
    self.gender       = nn.Sequential(nn.Dropout(p=dropout), nn.Linear(self.in_features,1000), nn.ReLU(), nn.Dropout(p=dropout), nn.Linear(1000,boolean))
    self.upcolor      = nn.Sequential(nn.Dropout(p=dropout), nn.Linear(self.in_features,1000), nn.ReLU(), nn.Dropout(p=dropout), nn.Linear(1000,upcolor))
    self.hair         = nn.Sequential(nn.Dropout(p=dropout), nn.Linear(self.in_features,1000), nn.ReLU(), nn.Dropout(p=dropout), nn.Linear(1000,boolean))

  def forward(self, x):
    """
    The function connects classifiers to the feature extractor
    to predict classes. 
    Return a dictionary
    """
    # print('x.type(): {}'.format(type(x)))
    x = self.feature_extractor(x)
    x = x.view(x.size(0), -1)
    # print('After fe x.type(): {}'.format(type(x)))
    
    return {
        'hat': self.hat(x),
        'handbag': self.handbag(x),
        'bag': self.bag(x),
        'backpack': self.bagpack(x),
        'up': self.up(x),
        'downcolor': self.downcolor(x),
        'clothes': self.clothes(x),
        'age': self.age(x),
        'down': self.down(x),
        'gender': self.gender(x),
        'upcolor': self.upcolor(x),
        'hair': self.hair(x)
    }




## Network fit

In [9]:
class network_fit(object):
  """
  Class for network, manage training, validation and test
  """

  def __init__ (self, model, device, train_dataloader, validation_dataloader, test_dataloader, lr):
    """
    Constructor
    generate a CNN
    """
    self.device = device
    self.model = model
    self.train_dataloader = train_dataloader
    self.validation_dataloader = validation_dataloader
    self.test_dataloader = test_dataloader
    self.cost_function = nn.CrossEntropyLoss()
    self.lr = lr
    self.optimizer = torch.optim.SGD(model.parameters(), lr=self.lr, momentum=0.9, weight_decay=0.001)
  
  
  def move_to(self, element):
    """
    Move dictionary or object to device
    """
    # Tensor
    if torch.is_tensor(element):
      # print('is tensor: {}'.format(element))
      return element.to(self.device)
    # Dictionary
    elif isinstance(element, dict):
      # print('is dictionary: {}'.format(element))
      dictionary = {}
      for key, value in element.items():
        dictionary[key] = self.move_to(value)
      return dictionary
    # List
    elif isinstance(element, list):
      # print('is list: {}'.format(element))
      lista = []
      for e in element:
        lista.append(self.move_to(e))
      return lista
    else:
      raise TypeError('Move to device: {} is failed.\n Invalid type of element: \n{}'.format(self.device, element))

  
  def loss(self, lables, output):
    """
    Calculate the loss in batch
    """
    batch_loss = 0.0
    # print('Lables: {} \n Output: {}'.format(lables, output))
    for key, value in lables.items():
      # print('output[key]: {} \nValue: {}'.format(output[key], value.type(torch.LongTensor)))
      batch_loss += self.cost_function(output[key], value.type(torch.LongTensor).to(self.device))
    return batch_loss

   
  def accuracy(self, truth_lables, output):
    """
    Calculate the accuracy on a single class
    """
    _, predictions = torch.max(output, dim=1)
    return predictions.eq(truth_lables).sum().item()

  
  def batch_accuracy_classifiers(self, truth_lables, output):
    """
    Calculate the accuracy on total number of classifiers (12)
    """
    tot_acc = {}
    for key, value in truth_lables.items():
      tot_acc[key] = self.accuracy(value, output[key])
    return tot_acc

 
  def total_comulative_accuracy(self, comulative_accuracy, batch_accuracy):
    """"
    Calculate the accuracy in all batches
    """
    if len(comulative_accuracy) == 0:
      return batch_accuracy
    for key, value in comulative_accuracy.items():
      comulative_accuracy[key] += batch_accuracy[key]
    return comulative_accuracy
 
  def get_results(self,img_id, outputs):
    """
    Return label results from model output
    """
    results = []
    results.append(img_id)
    for key, values in outputs.items():
      _, pred = torch.max(values, dim=1)
      results.append(int(pred.cpu().detach().numpy()[0]))
    return results

  def train_net(self, batch_size, num_lables = 12):
    """
    Specify the optimizers and train the network
    """
    print("Training model...")
    self.model.train()
    # Total train loss
    train_loss = 0.0
    # Accuracy
    comulative_accuracy = {}
    batch = samples = 0

    # Iteration in dataloader
    for id, data in enumerate(tqdm(self.train_dataloader)):
      input_img = data['pic'].to(self.device)
      truth_lables = self.move_to(data['lables'])
      # Predictions
      output = model(input_img.float())
      output = self.move_to(output)
      # Batch loss
      batch_loss = self.loss(truth_lables, output)
      # Backward
      batch_loss.backward()
      # Weights update
      self.optimizer.step()
      # Gradient to zero
      self.optimizer.zero_grad()
      # Train Loss
      train_loss += batch_loss/num_lables
      # Accuracy
      batch_accuracy = self.batch_accuracy_classifiers(truth_lables, output)
      comulative_accuracy = self.total_comulative_accuracy(comulative_accuracy, batch_accuracy)
      # Batch size
      samples += input_img.shape[0]
      batch+=1

    # Normalization accuracy
    for key, value in comulative_accuracy.items():
      comulative_accuracy[key] = value/samples
    # Normalization loss
    batch_loss = train_loss/batch
    
    return batch_loss, comulative_accuracy


  
  def validation_net(self, batch_size, num_lables = 12):
    """
    Specify the optimizers and validate the network
    """
    print("Validation model...")
    self.model.eval()
    # Total validatoin loss
    validation_loss = 0.0
    # Accuracy
    comulative_accuracy = {}
    batch =  samples = 0

    # Iteration in dataloader
    with torch.no_grad(): # reduce memory usage
      for id, data in enumerate(tqdm(self.validation_dataloader)):
        # print('data.pic: {}'.format(data['pic'].size()))
        input_img = data['pic'].to(self.device)
        truth_lables = self.move_to(data['lables'])
        # Predictions
        output =  self.move_to(model(input_img.float()))
        # Batch loss
        batch_loss = self.loss(truth_lables, output)
        # Validation Loss
        validation_loss += batch_loss/num_lables
        # Accuracy
        batch_accuracy = self.batch_accuracy_classifiers(truth_lables, output)
        comulative_accuracy = self.total_comulative_accuracy(comulative_accuracy, batch_accuracy)
        # Batch size
        samples += input_img.shape[0]
        batch+=1

      # Normalization accuracy
      for key, value in comulative_accuracy.items():
        comulative_accuracy[key] = value/samples
      # Normalization loss
      batch_loss = validation_loss/batch
      
      return batch_loss, comulative_accuracy


  def test_net(self):
    """
    Test the model and return predictions in a list object
    """ 
    print("Testing model...")
    self.model.eval()

    preds = []
    # Iteration in dataloader
    with torch.no_grad(): # reduce memory usage
      for id, data in enumerate(tqdm(self.test_dataloader)):
        input_img = data['pic'].to(self.device)
        # print('filename: {}'.format(data['filename'][0]))
        input_img_filename = str(data['filename'][0])
        # Predictions
        output = self.move_to(model(input_img.float()))
        # print('Output: {}'.format(output))
        # Results
        res = self.get_results(input_img_filename, output)
        # print('results: {}'.format(res))
        # Preds
        preds.append(res)
    return preds

  def post_processing(self, predictions_csv_path = './gdrive/MyDrive/DL/predictions.csv', final_csv_path = './gdrive/MyDrive/DL/classification_test.csv', predictions = None):
    """
    @param predictions_csv_path: './gdrive/MyDrive/DL/predictions.csv'
    @param final_csv_path: './gdrive/MyDrive/DL/classification_test.csv'
    @param predictions: the predictions in the list shape
    """
    if (predictions is None):
      predictions_df = pd.read_csv(predictions_csv_path)
    else:
      predictions_df = pd.DataFrame(predictions, columns=train_df.columns.to_list())
      predictions_df.to_csv(predictions_csv_path, index=False)

    # Inverse transformation of label encoder upcolor and downcolor
    predictions_df['upcolor'] = labenc_up.inverse_transform(predictions_df['upcolor'].astype(int))
    predictions_df['downcolor'] = labenc_down.inverse_transform(predictions_df['downcolor'].astype(int))
    colors_df = pd.get_dummies(predictions_df[['upcolor', 'downcolor']], prefix='', prefix_sep = '')
    predictions_df = pd.concat([predictions_df, colors_df], axis = 1).drop(['upcolor', 'downcolor'], axis=1)
    predictions_df = predictions_df.rename(columns={'filename': 'id'})

    # Check columns in predictions_df that are not in the original dataset
    print("Columns of original df are not in prediction_df: {}".format([col for col in df.columns.to_list() if col not in predictions_df.columns.to_list()]))
    print("Columns of prediction_df are not in the original df: {}".format([col for col in predictions_df.columns.to_list() if col not in df.columns.to_list()]))

    # Create the column that are not predicted
    cols_not_predicted = [col for col in df.columns.to_list() if col not in predictions_df.columns.to_list()]
    for col in cols_not_predicted:
      predictions_df[col] = 0

    # Rearrange columns in the original order and append multicolor_columns
    multicolor_columns = [col for col in predictions_df.columns.to_list() if col not in df.columns.to_list()]
    ordered_columns = df.columns.to_list()
    ordered_columns.extend(multicolor_columns)
    predictions_df = predictions_df[ordered_columns]

    # Adding 1 to each int element as the original dataset
    predictions_df.iloc[predictions_df.index, 1:]  = predictions_df.iloc[predictions_df.index, 1:] + 1

    # Save file
    predictions_df.to_csv('./gdrive/MyDrive/DL/classification_test.csv')
    return predictions_df


# Preprocessing

## Lable-encoding and One-Hot-Encoding
L'approccio di riferimento prevede di trasformare l'intero dataset con il OHE in modo da avere un dataset pulito che per ogni lable possa avere 1 o 0. Prima di fare questo bisogna trasformare quello che giá abbiamo in 

In [10]:
df = pd.read_csv(annotation_path)
df.head()

id  age  backpack  bag  handbag  clothes  down  up  hair  hat  gender  \
0   474    2         1    1        1        1     2   2     2    1       2   
1   857    2         1    2        1        2     2   2     2    1       2   
2  1487    2         2    1        1        2     2   2     1    1       1   
3  1422    2         1    2        1        2     2   2     1    1       1   
4   856    2         2    1        1        2     2   2     2    1       2   

   upblack  upwhite  upred  uppurple  upyellow  upgray  upblue  upgreen  \
0        1        2      1         1         1       1       1        1   
1        2        1      1         1         1       1       1        1   
2        2        1      1         1         1       1       1        1   
3        1        2      1         1         1       1       1        1   
4        1        2      1         1         1       1       1        1   

   downblack  downwhite  downpink  downpurple  downyellow  downgray  downblue  \
0          1          2         1           1           1         1         1   
1          1          1         1           1           1         1         1   
2          1          1         1           1           1         1         2   
3          2          1         1           1           1         1         1   
4          2          1         1           1           1         1         1   

   downgreen  downbrown  
0          1          1  
1          1          2  
2          1          1  
3          1          1  
4          1          1

In [11]:
# Extract list of image names
imgs = get_image_files(train_path)
get_image_name = lambda x: str(x).split('/')[-1]
imgs = list(map(get_image_name, imgs))
id_list = [int(x.split('_')[0]) for x in imgs]
ids_imgs_df = pd.DataFrame(zip(id_list, imgs), columns=['id', 'filename'])
ids_imgs_df.head()

id               filename
0   647  0647_c6_050521699.jpg
1   469  0469_c3_000669184.jpg
2  1478  1478_c2_029282298.jpg
3   426  0426_c3_033045601.jpg
4   983  0983_c1_015717273.jpg

In [12]:
# Unisco entrambe i df per avere i filename come index
annotation_df = pd.merge(df, ids_imgs_df, on='id')
# subtract 1 per iniziare da 0 taranne id e filename
annotation_df[annotation_df.columns[1:-1]] = annotation_df[annotation_df.columns[1:-1]].subtract(1)
annotation_df.head()

id  age  backpack  bag  handbag  clothes  down  up  hair  hat  gender  \
0  474    1         0    0        0        0     1   1     1    0       1   
1  474    1         0    0        0        0     1   1     1    0       1   
2  474    1         0    0        0        0     1   1     1    0       1   
3  474    1         0    0        0        0     1   1     1    0       1   
4  474    1         0    0        0        0     1   1     1    0       1   

   upblack  upwhite  upred  uppurple  upyellow  upgray  upblue  upgreen  \
0        0        1      0         0         0       0       0        0   
1        0        1      0         0         0       0       0        0   
2        0        1      0         0         0       0       0        0   
3        0        1      0         0         0       0       0        0   
4        0        1      0         0         0       0       0        0   

   downblack  downwhite  downpink  downpurple  downyellow  downgray  downblue  \
0          0          1         0           0           0         0         0   
1          0          1         0           0           0         0         0   
2          0          1         0           0           0         0         0   
3          0          1         0           0           0         0         0   
4          0          1         0           0           0         0         0   

   downgreen  downbrown               filename  
0          0          0  0474_c5_052589471.jpg  
1          0          0  0474_c3_078841428.jpg  
2          0          0  0474_c5_043687410.jpg  
3          0          0  0474_c5_003573345.jpg  
4          0          0  0474_c4_060726847.jpg

Problema con multi-color clothing. 

"It turns out however that for instances of persons that have multi-color clothing (eg. striped black and white shirt) all respective color attributes are set to NO.

Please handle this case by adding a further color category for upper and lower body clothing named 'upmulticolor' and 'downmulticolor' which is set to YES when no color attribute is set in the original dataset. In this way the number of categories to predict for upper body clothing becomes 9 and the number of categories to predict for lower body clothing becomes 10."

In [13]:
# Inserisco nuove colonne che mi rappresentano i vestiti che non hanno colori unici ma sono multicolor. Valorizzo 1 se la somma degli up/down color é 0, altrimenti 0
annotation_df=annotation_df.assign(upmulticolor=np.where(annotation_df.iloc[annotation_df.index,11:19].sum(axis=1)==0, 1, 0))
annotation_df=annotation_df.assign(downmulticolor=np.where(annotation_df.iloc[annotation_df.index,19:28].sum(axis=1)==0, 1, 0))
# Encode upcolors and downcolors
upcolors_columns = annotation_df.columns[11:19].to_list() + ['upmulticolor']
downcolors_columns = annotation_df.columns[19:28].to_list() + ['downmulticolor']
annotation_df['upcolor'] =annotation_df[upcolors_columns].idxmax(axis=1)
annotation_df['downcolor'] =annotation_df[downcolors_columns].idxmax(axis=1)
# Label Encoding
labenc_up = LabelEncoder()
labenc_down = LabelEncoder()
annotation_df.upcolor = labenc_up.fit_transform(annotation_df.upcolor)
annotation_df.downcolor = labenc_down.fit_transform(annotation_df.downcolor)
# Reduces columns 
annotation_df = annotation_df[list(set(annotation_df.columns) - set(upcolors_columns + downcolors_columns))]
annotation_df = annotation_df[['id', 'filename'] + list(set(annotation_df.columns.to_list()) - set(['id', 'filename']))]
# Save annotation
annotation_df.to_csv(current_dir+'/preprocessed_annotation.csv', index=False)
annotation_df

id               filename  up  downcolor  hat  bag  clothes  age  \
0       474  0474_c5_052589471.jpg   1          8    0    0        0    1   
1       474  0474_c3_078841428.jpg   1          8    0    0        0    1   
2       474  0474_c5_043687410.jpg   1          8    0    0        0    1   
3       474  0474_c5_003573345.jpg   1          8    0    0        0    1   
4       474  0474_c4_060726847.jpg   1          8    0    0        0    1   
...     ...                    ...  ..        ...  ...  ...      ...  ...   
12984  1177  1177_c2_053033722.jpg   1          8    0    0        1    1   
12985  1177  1177_c6_001668358.jpg   1          8    0    0        1    1   
12986  1177  1177_c2_029259193.jpg   1          8    0    0        1    1   
12987  1177  1177_c3_037640775.jpg   1          8    0    0        1    1   
12988  1177  1177_c6_078276224.jpg   1          8    0    0        1    1   

       upcolor  hair  handbag  gender  down  backpack  
0            7     1        0       1     1         0  
1            7     1        0       1     1         0  
2            7     1        0       1     1         0  
3            7     1        0       1     1         0  
4            7     1        0       1     1         0  
...        ...   ...      ...     ...   ...       ...  
12984        7     1        0       1     1         1  
12985        7     1        0       1     1         1  
12986        7     1        0       1     1         1  
12987        7     1        0       1     1         1  
12988        7     1        0       1     1         1  

[12989 rows x 14 columns]

# Dataframes
Train e validatoin dataset sono randomly splitted in 80/20 prendendo come riferimento gli ids.
Test dataset contiene solo i filename

In [14]:
## Annotation train 
annotation_df = pd.read_csv(current_dir+'/preprocessed_annotation.csv')
# Rearrange columns
cols = ['id', 'filename','hat','handbag','bag','backpack','up','downcolor','clothes','age','down','gender','upcolor','hair']
annotation_df = annotation_df[cols]
annotation_df.head()

id               filename  hat  handbag  bag  backpack  up  downcolor  \
0  474  0474_c5_052589471.jpg    0        0    0         0   1          8   
1  474  0474_c3_078841428.jpg    0        0    0         0   1          8   
2  474  0474_c5_043687410.jpg    0        0    0         0   1          8   
3  474  0474_c5_003573345.jpg    0        0    0         0   1          8   
4  474  0474_c4_060726847.jpg    0        0    0         0   1          8   

   clothes  age  down  gender  upcolor  hair  
0        0    1     1       1        7     1  
1        0    1     1       1        7     1  
2        0    1     1       1        7     1  
3        0    1     1       1        7     1  
4        0    1     1       1        7     1

In [15]:
## Test dataframe
# Extract list of image names
imgs = get_image_files(test_path)
get_image_name = lambda x: str(x).split('/')[-1]
imgs = list(map(get_image_name, imgs))

test_df = pd.DataFrame(imgs, columns=['filename'])
test_df.to_csv('{}/test_annotation.csv'.format(current_dir), index=False)
test_df.head()

test_csv = 'test_annotation.csv'
test_df = pd.read_csv(test_csv)
test_df.head()

filename
0  004339.jpg
1  012897.jpg
2  013665.jpg
3  010087.jpg
4  014884.jpg

In [16]:
## Train and validation split
# Randomly split ids
idxs = annotation_df.id.unique()
train_idxs,validation_idxs  = sklearn.model_selection.train_test_split(idxs, train_size=0.8)
print('Train_idxs: {}'.format(len(train_idxs)))
print('Validation_idxs: {}'.format(len(validation_idxs)))
print('All idx: {}'.format(len(idxs)))
# Transform Dataframe
train_df = annotation_df[annotation_df.id.isin(train_idxs)]
train_df = train_df.drop(['id'], axis=1)
val_df = annotation_df[annotation_df.id.isin(validation_idxs)]
val_df = val_df.drop(['id'], axis=1)
print('Train DataFrame len: {}'.format(len(train_df)))
print('Validation DataFrame len: {}'.format(len(val_df)))
# Save
train_df.to_csv(current_dir + '/train.csv', index=False)
val_df.to_csv(current_dir + '/validation.csv', index=False)

Train_idxs: 600
Validation_idxs: 151
All idx: 751
Train DataFrame len: 10229
Validation DataFrame len: 2760


In [17]:
def show_images(images, nmax=32):
    fig, ax = plt.subplots(figsize=(8, 8))
    ax.set_xticks([]); ax.set_yticks([])
    ax.imshow(make_grid(images['pic'][:nmax], nrow=8).squeeze().permute(1,2,0).clamp(0,1))
def show_batch(dl, nmax=32):
    for images in dl:
        show_images(images, nmax)
        break


# Pipelines
A pipeline that allows you to change settings and cycle in order to have data from the model to be able to analyze it.

1. Initialize the transformations
2. Create the datasets
3. Create the dataloaders
4. Initialize the model
5. Set the training settings
6. Initialize writers for analytics
7. Cycle between the ages
   8. Training and validation
   9. Save the data in a dataframe
10. Close the writers for analytics
11. Testing
12. Saving the results

## Testing transformations

In [ ]:
# Transformations
imagenet_stats = ([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
tfms_train0 =  tt.Compose([
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats,inplace=True)
])
tfms_train1 =  tt.Compose([
    tt.ToPILImage(),
    tt.RandomCrop((128, 64), padding=8, padding_mode='reflect'),
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats,inplace=True)
])

tfms_train2 =  tt.Compose([
    tt.ToPILImage(),
    tt.RandomCrop((128, 64), padding=8, padding_mode='reflect'),
    tt.RandomHorizontalFlip(p=0.5), 

    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats,inplace=True)
])

tfms_train3 =  tt.Compose([
    tt.ToPILImage(),
    tt.RandomRotation(10),
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats,inplace=True)
])

tfms_train4 =  tt.Compose([
    tt.ToPILImage(),
    tt.RandomHorizontalFlip(p=0.5), 
    tt.RandomRotation(10),
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats,inplace=True)
])

tfms_train5 =  tt.Compose([
    tt.ToPILImage(),
    tt.RandomCrop((128, 64), padding=8, padding_mode='reflect'),
    tt.RandomHorizontalFlip(p=0.5), 
    tt.RandomRotation(10),
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats,inplace=True)
])

tfms_train6 =  tt.Compose([
    tt.ToPILImage(),
    tt.RandomCrop((128, 64), padding=8, padding_mode='reflect'),
    tt.RandomHorizontalFlip(p=0.5), 
    tt.RandomRotation(10),
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats,inplace=True), 
    tt.RandomErasing(p=0.5, inplace=True)
])

tfms_train_list = [tfms_train0, tfms_train1, tfms_train2, tfms_train3, tfms_train4, tfms_train5, tfms_train6]

tfms_valid = tt.Compose([
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats)
])

tfms_test = tt.Compose([
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats, inplace=True)
])

# Base Training settings
settings = {
    'epochs': 64,
    'batch_size': 32,
    'stop_epoch': 10,
    'learning_rate': 1e-5
}

for times in range(0,5):
  # Initialize model
  device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
  model = CustomRNet50().to(device)
  if (next(model.parameters()).is_cuda):
    print('Model on GPU!!')
  # No improvements counter
  epochs_no_improve = 0
  # Validation and Test are always the same
  validation_ds = Dataset1501(csv_file = '{}/validation.csv'.format(current_dir), root_dir = train_path, transform=tfms_valid)
  test_ds = TestDataset1501(csv_file = test_csv, root_dir = test_path, transform=tfms_test)
  validation_dl = DataLoader(validation_ds, batch_size = settings['batch_size'], shuffle = True, num_workers = 2, pin_memory = True)
  test_dl = torch.utils.data.DataLoader(test_ds, batch_size = settings['batch_size'], num_workers = 2,pin_memory = True)

  transformation_counter = 0
  trans_pe = []
  # Itero sulle diverse trasformazioni di training
  for tfms_train in tfms_train_list:
    # Test transformation settings
    min_val_loss = np.Inf 
    # Training classes
    train_ds = Dataset1501(csv_file = '{}/train.csv'.format(current_dir), root_dir = train_path , transform = tfms_train)
    train_dl = DataLoader(train_ds, batch_size = settings['batch_size'], shuffle = True, num_workers = 2, pin_memory = True)
    net_fit = network_fit(model, device, train_dl, validation_dl, test_dl, lr = settings['learning_rate'])

    for epoch in range(settings['epochs']):
      tot_train_accuracy = tot_validation_accuracy = 0.0
      print('|epoch {}/{}'.format(epoch + 1, settings['epochs']))

      ## Training
      train_loss, train_accuracy = net_fit.train_net(batch_size = settings['batch_size'])
      # Print training
      print_text = '|train_loss: {:.3f}'.format(train_loss.data)
      for key, value in train_accuracy.items():
        tot_train_accuracy += value
      print_text += '|avg_val_acc: {:.3f}'.format(tot_train_accuracy/len(train_accuracy))
      print(print_text)
      
      ## Validation
      valid_loss, valid_accuracy = net_fit.validation_net(batch_size = settings['batch_size'])
      # Print validatoin
      print_text = '|val_loss: {:.3f}'.format(valid_loss.data)
      for key, value in valid_accuracy.items():
        tot_validation_accuracy += value 
      print_text += '|avg_val_acc: {:.3f}'.format(tot_validation_accuracy/len(valid_accuracy))
      print(print_text)

      # Early stopping
      if (valid_loss < min_val_loss):
        torch.save(model, '{}/model.pth'.format(current_dir))
        epochs_no_improve = 0
        min_val_loss = valid_loss
        # save performance evaluation of last model saved
        last_saved = [transformation_counter, 
                      epoch + 1, 
                      float('{:.3f}'.format(float(train_loss.data.cpu()))), 
                      float('{:.3f}'.format(tot_train_accuracy/len(train_accuracy))),
                      float('{:.3f}'.format(float(valid_loss.data.cpu()))),
                      float('{:.3f}'.format(tot_validation_accuracy/len(valid_accuracy)))]
        print('|Model saved')
      else:
        epochs_no_improve += 1
        if (epochs_no_improve == settings['stop_epoch']):
          print('|Early stopping')
          break
      print('Last performance saved: {}'.format(last_saved))
    # save performance evaluation
    trans_pe.append(last_saved)
    transformation_counter += 1
    print(trans_pe)


  df_trans_pe = pd.DataFrame(trans_pe, columns=['id_tran', 'epochs', 'train_loss', 'train_acc', 'valid_loss', 'valid_acc'])
  df_trans_pe.to_csv('./gdrive/MyDrive/DL/Evaluations/transformations_eval{}.csv'.format(times), index=False)

### Evaluation transformations

In [19]:
path = './gdrive/MyDrive/DL/Evaluations/transformations_eval'
all_files = glob.glob(path + "*.csv")
print(*all_files, sep='\n')
li = []

for filename in all_files:
    df = pd.read_csv(filename, index_col=None, header=0)
    li.append(df)

frame = pd.concat(li, axis=0, ignore_index=True)
frame.groupby(['id_tran']).mean().sort_values(['valid_acc'], ascending = False)

./gdrive/MyDrive/DL/Evaluations/transformations_eval0.csv
./gdrive/MyDrive/DL/Evaluations/transformations_eval1.csv
./gdrive/MyDrive/DL/Evaluations/transformations_eval4.csv
./gdrive/MyDrive/DL/Evaluations/transformations_eval3.csv
./gdrive/MyDrive/DL/Evaluations/transformations_eval2.csv


epochs  train_loss  train_acc  valid_loss  valid_acc
id_tran                                                      
4           7.4      0.0044     0.9988      0.8060     0.8608
3           3.6      0.0052     0.9984      0.7688     0.8604
5          14.0      0.0070     0.9980      0.7830     0.8584
2           3.8      0.0290     0.9906      0.7094     0.8570
6          14.4      0.0352     0.9884      0.6658     0.8560
1           1.8      0.0996     0.9654      0.6070     0.8514
0           2.0      0.4128     0.8462      0.4102     0.8508

## Testing hyperparameters

### Learning rates

In [ ]:
# Transformations
imagenet_stats = ([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
tfms_train =  tt.Compose([
    tt.ToPILImage(),
    tt.RandomHorizontalFlip(p=0.5), 
    tt.RandomRotation(10),
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats,inplace=True)
])

tfms_valid = tt.Compose([
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats)
])

tfms_test = tt.Compose([
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats, inplace=True)
])

# Base Training settings
setting_master = [
    {
    'epochs': 64,
    'batch_size': 32,
    'stop_epoch': 10,
    'learning_rate': 1e-4
    },
    {
    'epochs': 64,
    'batch_size': 32,
    'stop_epoch': 10,
    'learning_rate': 1e-3
    },
    {
    'epochs': 64,
    'batch_size': 32,
    'stop_epoch': 10,
    'learning_rate': 1e-2
    },
    {
    'epochs': 64,
    'batch_size': 32,
    'stop_epoch': 10,
    'learning_rate': 1e-1
    }
]

for times in range(0,5):
  # Initialize model
  device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
  model = CustomRNet50().to(device)
  if (next(model.parameters()).is_cuda):
    print('Model on GPU!!')
  # No improvements counter
  epochs_no_improve = 0
  
  transformation_counter = 0
  trans_pe = []
  # Itero sulle diverse trasformazioni di training
  for settings in setting_master:
    # Test transformation settings
    min_val_loss = np.Inf 
    # Validation and Test are always the same
    validation_ds = Dataset1501(csv_file = '{}/validation.csv'.format(current_dir), root_dir = train_path, transform=tfms_valid)
    test_ds = TestDataset1501(csv_file = test_csv, root_dir = test_path, transform=tfms_test)
    validation_dl = DataLoader(validation_ds, batch_size = settings['batch_size'], shuffle = True, num_workers = 2, pin_memory = True)
    test_dl = torch.utils.data.DataLoader(test_ds, batch_size = settings['batch_size'], num_workers = 2,pin_memory = True)
    # Training classes
    train_ds = Dataset1501(csv_file = '{}/train.csv'.format(current_dir), root_dir = train_path , transform = tfms_train)
    train_dl = DataLoader(train_ds, batch_size = settings['batch_size'], shuffle = True, num_workers = 2, pin_memory = True)
    net_fit = network_fit(model, device, train_dl, validation_dl, test_dl, lr = settings['learning_rate'])

    for epoch in range(settings['epochs']):
      tot_train_accuracy = tot_validation_accuracy = 0.0
      print('|epoch {}/{}'.format(epoch + 1, settings['epochs']))

      ## Training
      train_loss, train_accuracy = net_fit.train_net(batch_size = settings['batch_size'])
      # Print training
      print_text = '|train_loss: {:.3f}'.format(train_loss.data)
      for key, value in train_accuracy.items():
        tot_train_accuracy += value
      print_text += '|avg_val_acc: {:.3f}'.format(tot_train_accuracy/len(train_accuracy))
      print(print_text)
      
      ## Validation
      valid_loss, valid_accuracy = net_fit.validation_net(batch_size = settings['batch_size'])
      # Print validatoin
      print_text = '|val_loss: {:.3f}'.format(valid_loss.data)
      for key, value in valid_accuracy.items():
        tot_validation_accuracy += value 
      print_text += '|avg_val_acc: {:.3f}'.format(tot_validation_accuracy/len(valid_accuracy))
      print(print_text)

      # Early stopping
      if (valid_loss < min_val_loss):
        torch.save(model, '{}/model.pth'.format(current_dir))
        epochs_no_improve = 0
        min_val_loss = valid_loss
        # save performance evaluation of last model saved
        last_saved = [settings['learning_rate'], 
                      epoch + 1, 
                      float('{:.3f}'.format(float(train_loss.data.cpu()))), 
                      float('{:.3f}'.format(tot_train_accuracy/len(train_accuracy))),
                      float('{:.3f}'.format(float(valid_loss.data.cpu()))),
                      float('{:.3f}'.format(tot_validation_accuracy/len(valid_accuracy)))]
        print('|Model saved')
      else:
        epochs_no_improve += 1
        if (epochs_no_improve == settings['stop_epoch']):
          print('|Early stopping')
          break
      print('Last performance saved: {}'.format(last_saved))
    # save performance evaluation
    trans_pe.append(last_saved)
    transformation_counter += 1
    print(trans_pe)


  df_trans_pe = pd.DataFrame(trans_pe, columns=['lr', 'epochs', 'train_loss', 'train_acc', 'valid_loss', 'valid_acc'])
  df_trans_pe.to_csv('./gdrive/MyDrive/DL/Evaluations/lr_eval{}.csv'.format(times), index=False)

In [ ]:
path = './gdrive/MyDrive/DL/Evaluations/lr_eval'
all_files = glob.glob(path + "*.csv")
print(*all_files, sep='\n')
li = []

for filename in all_files:
    df = pd.read_csv(filename, index_col=None, header=0)
    li.append(df)

frame1 = pd.concat(li, axis=0, ignore_index=True)
frame1.groupby(['lr']).mean().sort_values(['valid_acc'], ascending = False)

./gdrive/MyDrive/DL/Evaluations/lr_eval0.csv
./gdrive/MyDrive/DL/Evaluations/lr_eval1.csv
./gdrive/MyDrive/DL/Evaluations/lr_eval2.csv


epochs  train_loss  train_acc  valid_loss  valid_acc
lr                                                             
0.0001  14.666667    0.311000   0.884000    0.404333   0.856000
0.0010   1.000000    0.223000   0.918000    0.490333   0.848000
0.0100   2.666667    0.387000   0.852000    0.459667   0.836667
0.1000  10.000000    0.446333   0.828667    0.493667   0.817333

In [ ]:
path = './gdrive/MyDrive/DL/Evaluations/lr_eval'
all_files = glob.glob(path + "*.csv")
print(*all_files, sep='\n')

./gdrive/MyDrive/DL/Evaluations/lr_eval0.csv
./gdrive/MyDrive/DL/Evaluations/lr_eval1.csv
./gdrive/MyDrive/DL/Evaluations/lr_eval2.csv


### Batch size

In [ ]:
# Transformations
imagenet_stats = ([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
tfms_train =  tt.Compose([
    tt.ToPILImage(),
    tt.RandomHorizontalFlip(p=0.5), 
    tt.RandomRotation(10),
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats,inplace=True)
])

tfms_valid = tt.Compose([
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats)
])

tfms_test = tt.Compose([
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats, inplace=True)
])

# Base Training settings
setting_master = [
    {
    'epochs': 150,
    'batch_size': 32,
    'stop_epoch': 10,
    'learning_rate': 1e-5
    },
    {
    'epochs': 150,
    'batch_size': 64,
    'stop_epoch': 10,
    'learning_rate': 1e-5
    },
    {
    'epochs': 150,
    'batch_size': 128,
    'stop_epoch': 10,
    'learning_rate': 1e-5
    }
]

for times in range(0,2):
  # Initialize model
  device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
  model = CustomRNet50().to(device)
  if (next(model.parameters()).is_cuda):
    print('Model on GPU!!')
  # No improvements counter
  epochs_no_improve = 0
  
  transformation_counter = 0
  trans_pe = []
  # Itero sulle diverse trasformazioni di training
  for settings in setting_master:
    # Test transformation settings
    min_val_loss = np.Inf 
    # Validation and Test are always the same
    validation_ds = Dataset1501(csv_file = '{}/validation.csv'.format(current_dir), root_dir = train_path, transform=tfms_valid)
    test_ds = TestDataset1501(csv_file = test_csv, root_dir = test_path, transform=tfms_test)
    validation_dl = DataLoader(validation_ds, batch_size = settings['batch_size'], shuffle = True, num_workers = 2, pin_memory = True)
    test_dl = torch.utils.data.DataLoader(test_ds, batch_size = settings['batch_size'], num_workers = 2,pin_memory = True)
    # Training classes
    train_ds = Dataset1501(csv_file = '{}/train.csv'.format(current_dir), root_dir = train_path , transform = tfms_train)
    train_dl = DataLoader(train_ds, batch_size = settings['batch_size'], shuffle = True, num_workers = 2, pin_memory = True)
    net_fit = network_fit(model, device, train_dl, validation_dl, test_dl, lr = settings['learning_rate'])

    for epoch in range(settings['epochs']):
      tot_train_accuracy = tot_validation_accuracy = 0.0
      print('|epoch {}/{}'.format(epoch + 1, settings['epochs']))

      ## Training
      train_loss, train_accuracy = net_fit.train_net(batch_size = settings['batch_size'])
      # Print training
      print_text = '|train_loss: {:.3f}'.format(train_loss.data)
      for key, value in train_accuracy.items():
        tot_train_accuracy += value
      print_text += '|avg_val_acc: {:.3f}'.format(tot_train_accuracy/len(train_accuracy))
      print(print_text)
      
      ## Validation
      valid_loss, valid_accuracy = net_fit.validation_net(batch_size = settings['batch_size'])
      # Print validatoin
      print_text = '|val_loss: {:.3f}'.format(valid_loss.data)
      for key, value in valid_accuracy.items():
        tot_validation_accuracy += value 
      print_text += '|avg_val_acc: {:.3f}'.format(tot_validation_accuracy/len(valid_accuracy))
      print(print_text)

      # Early stopping
      if (valid_loss < min_val_loss):
        torch.save(model, '{}/model.pth'.format(current_dir))
        epochs_no_improve = 0
        min_val_loss = valid_loss
        # save performance evaluation of last model saved
        last_saved = [settings['batch_size'], 
                      epoch + 1, 
                      float('{:.3f}'.format(float(train_loss.data.cpu()))), 
                      float('{:.3f}'.format(tot_train_accuracy/len(train_accuracy))),
                      float('{:.3f}'.format(float(valid_loss.data.cpu()))),
                      float('{:.3f}'.format(tot_validation_accuracy/len(valid_accuracy)))]
        print('|Model saved')
      else:
        epochs_no_improve += 1
        if (epochs_no_improve == settings['stop_epoch']):
          print('|Early stopping')
          break
      print('Last performance saved: {}'.format(last_saved))
    # save performance evaluation
    trans_pe.append(last_saved)
    transformation_counter += 1
    print(trans_pe)


  df_trans_pe = pd.DataFrame(trans_pe, columns=['batch_size', 'epochs', 'train_loss', 'train_acc', 'valid_loss', 'valid_acc'])
  df_trans_pe.to_csv('./gdrive/MyDrive/DL/Evaluations/batch_size_eval{}.csv'.format(times), index=False)

In [ ]:
path = './gdrive/MyDrive/DL/Evaluations/batch_size_eval'
all_files = glob.glob(path + "*.csv")
print(*all_files, sep='\n')
li = []

for filename in all_files:
    df = pd.read_csv(filename, index_col=None, header=0)
    li.append(df)

frame = pd.concat(li, axis=0, ignore_index=True)
frame.groupby(['batch_size']).mean().sort_values(['valid_acc'], ascending = False)

./gdrive/MyDrive/DL/Evaluations/batch_size_eval2.csv
./gdrive/MyDrive/DL/Evaluations/batch_size_eval0.csv
./gdrive/MyDrive/DL/Evaluations/batch_size_eval1.csv


epochs  train_loss  train_acc  valid_loss  valid_acc
batch_size                                                          
128           4.000000    0.276333   0.898333    0.406333   0.855000
64            5.000000    0.295000   0.891000    0.404000   0.854000
32          123.666667    0.331667   0.877000    0.408000   0.852667

# Final model


In [18]:
# Transformations
imagenet_stats = ([0.485, 0.456, 0.406], [0.229, 0.224, 0.225])
tfms_train =  tt.Compose([
    tt.ToPILImage(),
    tt.RandomHorizontalFlip(p=0.5), 
    tt.RandomRotation(10),
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats,inplace=True)
])

tfms_valid = tt.Compose([
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats)
])

tfms_test = tt.Compose([
    tt.ToTensor(), 
    tt.Normalize(*imagenet_stats, inplace=True)
])

# Base Training settings
setting_master = [
    {
    'epochs': 400,
    'batch_size': 128,
    'stop_epoch': 10,
    'learning_rate': 1e-5
    }
]

for times in range(0,1):
  # Initialize model
  device = torch.device('cuda') if torch.cuda.is_available() else torch.device('cpu')
  model = CustomRNet50().to(device)
  if (next(model.parameters()).is_cuda):
    print('Model on GPU!!')
  # No improvements counter
  epochs_no_improve = 0
  
  transformation_counter = 0
  trans_pe = []
  # Itero sulle diverse trasformazioni di training
  for settings in setting_master:
    # Test transformation settings
    min_val_loss = np.Inf 
    # Validation and Test are always the same
    validation_ds = Dataset1501(csv_file = '{}/validation.csv'.format(current_dir), root_dir = train_path, transform=tfms_valid)
    test_ds = TestDataset1501(csv_file = test_csv, root_dir = test_path, transform=tfms_test)
    validation_dl = DataLoader(validation_ds, batch_size = settings['batch_size'], shuffle = True, num_workers = 2, pin_memory = True)
    test_dl = torch.utils.data.DataLoader(test_ds, batch_size = settings['batch_size'], num_workers = 2,pin_memory = True)
    # Training classes
    train_ds = Dataset1501(csv_file = '{}/train.csv'.format(current_dir), root_dir = train_path , transform = tfms_train)
    train_dl = DataLoader(train_ds, batch_size = settings['batch_size'], shuffle = True, num_workers = 2, pin_memory = True)
    net_fit = network_fit(model, device, train_dl, validation_dl, test_dl, lr = settings['learning_rate'])

    for epoch in range(settings['epochs']):
      tot_train_accuracy = tot_validation_accuracy = 0.0
      print('|epoch {}/{}'.format(epoch + 1, settings['epochs']))

      ## Training
      train_loss, train_accuracy = net_fit.train_net(batch_size = settings['batch_size'])
      # Print training
      print_text = '|train_loss: {:.3f}'.format(train_loss.data)
      for key, value in train_accuracy.items():
        tot_train_accuracy += value
      print_text += '|avg_val_acc: {:.3f}'.format(tot_train_accuracy/len(train_accuracy))
      print(print_text)
      
      ## Validation
      valid_loss, valid_accuracy = net_fit.validation_net(batch_size = settings['batch_size'])
      # Print validatoin
      print_text = '|val_loss: {:.3f}'.format(valid_loss.data)
      for key, value in valid_accuracy.items():
        tot_validation_accuracy += value 
      print_text += '|avg_val_acc: {:.3f}'.format(tot_validation_accuracy/len(valid_accuracy))
      print(print_text)

      # Early stopping
      if (valid_loss < min_val_loss):
        torch.save(model, '{}/model.pth'.format(current_dir))
        epochs_no_improve = 0
        min_val_loss = valid_loss
        # save performance evaluation of last model saved
        last_saved = [epoch + 1, 
                      float('{:.3f}'.format(float(train_loss.data.cpu()))), 
                      float('{:.3f}'.format(tot_train_accuracy/len(train_accuracy))),
                      float('{:.3f}'.format(float(valid_loss.data.cpu()))),
                      float('{:.3f}'.format(tot_validation_accuracy/len(valid_accuracy)))]
        print('|Model saved')
      else:
        epochs_no_improve += 1
        if (epochs_no_improve == settings['stop_epoch']):
          print('|Early stopping')
          break
      print('Last performance saved: {}'.format(last_saved))
    # save performance evaluation
    trans_pe.append(last_saved)
    transformation_counter += 1
    print(trans_pe)


  df_trans_pe = pd.DataFrame(trans_pe, columns=['epochs', 'train_loss', 'train_acc', 'valid_loss', 'valid_acc'])
  df_trans_pe.to_csv('./gdrive/MyDrive/DL/Evaluations/model_eval_final{}.csv'.format(times), index=False)

Downloading: "https://download.pytorch.org/models/resnet50-0676ba61.pth" to /root/.cache/torch/hub/checkpoints/resnet50-0676ba61.pth


  0%|          | 0.00/97.8M [00:00<?, ?B/s]

Model on GPU!!
root_dir: ./train
csv_file: ./validation.csv
root_dir: ./train
csv_file: ./train.csv
|epoch 1/400
Training model...


  0%|          | 0/80 [00:00<?, ?it/s]

|train_loss: 1.029|avg_val_acc: 0.430
Validation model...


...

|val_loss: 0.416|avg_val_acc: 0.849
Last performance saved: [389, 0.356, 0.869, 0.416, 0.848]
|epoch 399/400
Training model...


  0%|          | 0/80 [00:00<?, ?it/s]

|train_loss: 0.350|avg_val_acc: 0.871
Validation model...


  0%|          | 0/22 [00:00<?, ?it/s]

|val_loss: 0.418|avg_val_acc: 0.849
|Early stopping
[[389, 0.356, 0.869, 0.416, 0.848]]


In [19]:
%cp model.pth /grdive/MyDrive/DL/

cp: cannot create regular file '/grdive/MyDrive/DL/': No such file or directory


In [ ]:
path = './gdrive/MyDrive/DL/Evaluations/model_eval'
all_files = glob.glob(path + "*.csv")
print(*all_files, sep='\n')
li = []

for filename in all_files:
    df = pd.read_csv(filename, index_col=None, header=0)
    li.append(df)

frame1 = pd.concat(li, axis=0, ignore_index=True)
frame1.sort_values(['valid_acc'], ascending = False)

./gdrive/MyDrive/DL/Evaluations/model_eval1.csv
./gdrive/MyDrive/DL/Evaluations/model_eval2.csv
./gdrive/MyDrive/DL/Evaluations/model_eval0.csv


epochs  train_loss  train_acc  valid_loss  valid_acc
0      28       0.291      0.892       0.410      0.856
1      26       0.315      0.883       0.412      0.854
2      24       0.334      0.876       0.414      0.849

In [ ]:
# %load_ext tensorboard
# %reload_ext tensorboard
# %tensorboard --logdir=runs

# Post-Processing


In [ ]:
# Read predictions and save predictions from a stored file
model = torch.load('model.pth')
net_fit = network_fit(model, device, train_dl, validation_dl, test_dl, lr = settings['learning_rate'])
net_fit.post_processing()